In [1]:

# coding: utf-8

import numpy as np
from torchvision import transforms
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torch.autograd import Variable
import sys
from new_loss import DiscriminativeLoss
import torchvision.models as models
from torch.nn import DataParallel
import torchvision.utils as vutils
from tensorboardX import SummaryWriter
from sklearn.metrics import jaccard_score as jacc
from pycocotools.coco import COCO


# from dataloaders import make_data_loader
from modeling.sync_batchnorm.replicate import patch_replication_callback
from modeling.deeplab import *
from utils.loss import SegmentationLosses
from utils.calculate_weights import calculate_weigths_labels
from utils.lr_scheduler import LR_Scheduler
from utils.saver import Saver
# from utils.summaries import TensorboardSummary
from utils.metrics import Evaluator
from utils.metrics import get_bin_map

writer = SummaryWriter()




model = DeepLab(num_classes=21,
                backbone='resnet',
                )




In [5]:
for c in model.children():
    print(c)

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): SynchronizedBatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace)
      (downsample): Sequential(
        (0): Conv2d(64

In [7]:
# model = DataParallel(model)
checkpoint = torch.load('deeplab-resnet.pth.tar',map_location='cpu')
state = model.state_dict()
state.update(checkpoint['state_dict'])
model.load_state_dict(state)


# model.load_state_dict(checkpoint['state_dict'])


In [33]:
checkpoint['best_pred']

0.7843039426122174

In [10]:
len(model.parameters())

TypeError: object of type 'generator' has no len()

In [18]:
i = 0
for mod in model.named_children():
    print(mod,i,len(mod))
    i+=1

('backbone', ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): SynchronizedBatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): SynchronizedBatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace)
      (downsample): Sequential(
        (

In [ ]:
wget --load-cookies /tmp/cookies.txt "https://docs.google.com/uc?export=download&confirm=$(wget --quiet --save-cookies /tmp/cookies.txt --keep-session-cookies --no-check-certificate 'https://docs.google.com/uc?export=download&id=FILEID' -O- | sed -rn 's/.*confirm=([0-9A-Za-z_]+).*/\1\n/p')&id=FILEID" -O FILENAME && rm -rf /tmp/cookies.txt

In [29]:
# freeze all
for param in model.parameters():
    param.requires_grad = False
    
# unfreeze lastconv2
for name, child in model.named_children():
            if name == 'decoder':
                for n,c in child.named_children():
                    if n == 'last_conv2':
                        for param in c.parameters():
                            param.requires_grad = True
                                

In [30]:
for param in model.parameters():
    print(param)


Parameter containing:
tensor([[[[ 1.4587e-02,  9.5933e-04, -7.4720e-03,  ..., -6.6904e-03,
            7.3701e-04,  9.5040e-03],
          [ 2.6121e-03,  4.9495e-03, -5.4276e-03,  ..., -3.9156e-02,
           -3.4436e-02, -1.4963e-02],
          [ 4.9470e-03,  1.5524e-02,  2.6544e-02,  ...,  1.8064e-02,
            7.9475e-03,  1.7200e-02],
          ...,
          [-2.0759e-02, -6.5110e-02, -1.4781e-01,  ..., -1.8076e-01,
           -6.4527e-02,  2.0758e-02],
          [ 3.7715e-03,  8.6257e-03,  1.3672e-03,  ..., -8.0314e-02,
           -8.9835e-02, -4.7096e-02],
          [-1.8577e-02, -8.6754e-03,  2.1521e-02,  ...,  7.7088e-02,
            4.7291e-02, -7.4712e-03]],

         [[ 8.0141e-03, -5.2389e-05, -4.3155e-03,  ..., -6.1800e-03,
            8.6068e-03,  1.3582e-02],
          [ 5.3134e-04,  8.4129e-03, -8.2458e-04,  ..., -3.6543e-02,
           -2.7102e-02, -6.2386e-03],
          [ 1.2880e-03,  1.8387e-02,  3.9745e-02,  ...,  4.5308e-02,
            2.6051e-02,  1.9970e-02]

Parameter containing:
tensor([[[[ 1.7075e-03]],

         [[-6.7153e-04]],

         [[ 1.6522e-03]],

         ...,

         [[-1.4251e-03]],

         [[ 2.7394e-04]],

         [[ 3.2131e-03]]],


        [[[ 9.1824e-05]],

         [[ 2.1925e-04]],

         [[ 2.1380e-05]],

         ...,

         [[-1.3759e-04]],

         [[-3.4729e-06]],

         [[ 5.9853e-04]]],


        [[[ 1.1345e-02]],

         [[ 1.0639e-03]],

         [[-1.6789e-03]],

         ...,

         [[ 3.7873e-03]],

         [[ 8.9925e-03]],

         [[ 3.8450e-03]]],


        ...,


        [[[ 1.6528e-03]],

         [[-1.2100e-03]],

         [[ 3.1257e-05]],

         ...,

         [[ 1.2010e-03]],

         [[ 1.1499e-04]],

         [[-4.9982e-04]]],


        [[[-1.8071e-03]],

         [[ 3.5320e-03]],

         [[-2.8610e-03]],

         ...,

         [[ 2.2588e-03]],

         [[ 2.5160e-04]],

         [[ 2.7925e-03]]],


        [[[-4.2722e-03]],

         [[-4.4475e-04]],

         [[-6.

Parameter containing:
tensor([0.1415, 0.1027, 0.1185, 0.1100, 0.1352, 0.1570, 0.0924, 0.0606, 0.1382,
        0.0887, 0.1104, 0.0893, 0.0835, 0.1132, 0.1417, 0.1160, 0.1117, 0.1170,
        0.1414, 0.1324, 0.1324, 0.1632, 0.1255, 0.1049, 0.1224, 0.1385, 0.1167,
        0.1438, 0.1243, 0.1375, 0.1270, 0.1391, 0.1059, 0.1197, 0.1337, 0.1136,
        0.1370, 0.1498, 0.1308, 0.1395, 0.1528, 0.1459, 0.1291, 0.1451, 0.1521,
        0.1316, 0.1285, 0.1289, 0.1349, 0.1607, 0.1758, 0.1211, 0.1314, 0.1312,
        0.1398, 0.0958, 0.1521, 0.1508, 0.1423, 0.1411, 0.1415, 0.1452, 0.1642,
        0.0965, 0.1274, 0.1360, 0.1270, 0.1597, 0.0976, 0.1348, 0.1377, 0.1390,
        0.1413, 0.1361, 0.1442, 0.1293, 0.1355, 0.1038, 0.0893, 0.1334, 0.1337,
        0.1002, 0.1372, 0.1575, 0.1602, 0.1153, 0.1264, 0.1533, 0.1303, 0.1190,
        0.1394, 0.1295, 0.1504, 0.1265, 0.0816, 0.1273, 0.1158, 0.0912, 0.1496,
        0.1248, 0.1001, 0.1430, 0.1045, 0.1540, 0.0740, 0.1372, 0.1462, 0.1039,
        0.1606, 0.

Parameter containing:
tensor([-1.2273e-01, -2.3905e-01, -1.9913e-01, -2.0642e-01, -1.3045e-01,
        -1.5135e-01, -1.7890e-01, -1.2307e-01, -1.6949e-01, -1.6143e-01,
        -1.5050e-01, -1.6151e-01, -1.7535e-01, -7.1144e-02, -1.5682e-01,
        -1.7271e-01, -1.3887e-01, -2.1029e-01, -1.7074e-01, -1.9235e-01,
        -1.5974e-01, -1.2320e-01, -2.2679e-01, -1.3480e-01, -1.7788e-01,
        -1.0459e-01, -1.3766e-01, -1.5401e-01, -1.5326e-01, -8.7404e-02,
        -1.9629e-01, -1.7384e-01, -1.6139e-01, -1.7797e-01, -1.6713e-01,
        -1.3534e-01, -4.6887e-02, -1.6963e-01, -1.3415e-01, -9.1138e-02,
        -1.4244e-01, -1.3307e-01, -1.3382e-01, -1.4614e-01, -7.9006e-02,
        -1.8496e-01, -1.6375e-01, -1.1104e-01, -1.7440e-01, -1.6994e-01,
        -9.9283e-02, -1.7207e-01, -2.0494e-01, -2.0189e-01, -1.3472e-01,
        -1.6653e-01, -2.2992e-01, -3.3266e-02, -6.9946e-02, -1.5152e-01,
        -1.8168e-01, -1.7995e-01, -1.0506e-01, -6.9859e-02, -1.3394e-01,
        -1.8151e-01, -1.8098e

In [31]:
model.state_dict()

OrderedDict([('backbone.conv1.weight',
              tensor([[[[ 1.4587e-02,  9.5933e-04, -7.4720e-03,  ..., -6.6904e-03,
                          7.3701e-04,  9.5040e-03],
                        [ 2.6121e-03,  4.9495e-03, -5.4276e-03,  ..., -3.9156e-02,
                         -3.4436e-02, -1.4963e-02],
                        [ 4.9470e-03,  1.5524e-02,  2.6544e-02,  ...,  1.8064e-02,
                          7.9475e-03,  1.7200e-02],
                        ...,
                        [-2.0759e-02, -6.5110e-02, -1.4781e-01,  ..., -1.8076e-01,
                         -6.4527e-02,  2.0758e-02],
                        [ 3.7715e-03,  8.6257e-03,  1.3672e-03,  ..., -8.0314e-02,
                         -8.9835e-02, -4.7096e-02],
                        [-1.8577e-02, -8.6754e-03,  2.1521e-02,  ...,  7.7088e-02,
                          4.7291e-02, -7.4712e-03]],
              
                       [[ 8.0141e-03, -5.2389e-05, -4.3155e-03,  ..., -6.1800e-03,
                       

In [13]:
checkpoint['state_dict']

OrderedDict([('backbone.conv1.weight',
              tensor([[[[ 1.4587e-02,  9.5933e-04, -7.4720e-03,  ..., -6.6904e-03,
                          7.3701e-04,  9.5040e-03],
                        [ 2.6121e-03,  4.9495e-03, -5.4276e-03,  ..., -3.9156e-02,
                         -3.4436e-02, -1.4963e-02],
                        [ 4.9470e-03,  1.5524e-02,  2.6544e-02,  ...,  1.8064e-02,
                          7.9475e-03,  1.7200e-02],
                        ...,
                        [-2.0759e-02, -6.5110e-02, -1.4781e-01,  ..., -1.8076e-01,
                         -6.4527e-02,  2.0758e-02],
                        [ 3.7715e-03,  8.6257e-03,  1.3672e-03,  ..., -8.0314e-02,
                         -8.9835e-02, -4.7096e-02],
                        [-1.8577e-02, -8.6754e-03,  2.1521e-02,  ...,  7.7088e-02,
                          4.7291e-02, -7.4712e-03]],
              
                       [[ 8.0141e-03, -5.2389e-05, -4.3155e-03,  ..., -6.1800e-03,
                       